In [27]:
import fitbit
import gather_keys_oauth2 as Oauth2
import pandas as pd 
import datetime
import plotly.express as px
import time

CLIENT_ID = '23BLLK'
CLIENT_SECRET = '03fe879abe48c44e91dfd4339ea88847'


yesterday = str((datetime.datetime.now() - datetime.timedelta(days=1)).strftime("%Y%m%d"))
yesterday2 = str((datetime.datetime.now() - datetime.timedelta(days=1)).strftime("%Y-%m-%d"))
today = str(datetime.datetime.now().strftime("%Y%m%d"))

In [8]:
server = Oauth2.OAuth2Server(CLIENT_ID, CLIENT_SECRET)
server.browser_authorize()
ACCESS_TOKEN = str(server.fitbit.client.session.token['access_token'])
REFRESH_TOKEN = str(server.fitbit.client.session.token['refresh_token'])
auth2_client = fitbit.Fitbit(CLIENT_ID, CLIENT_SECRET, oauth2=True, access_token=ACCESS_TOKEN, refresh_token=REFRESH_TOKEN)

[12/Nov/2021:11:37:28] ENGINE Listening for SIGTERM.
[12/Nov/2021:11:37:28] ENGINE Listening for SIGHUP.
[12/Nov/2021:11:37:28] ENGINE Listening for SIGUSR1.
[12/Nov/2021:11:37:28] ENGINE Bus STARTING
CherryPy Checker:
The Application mounted at '' has an empty config.

[12/Nov/2021:11:37:28] ENGINE Started monitor thread 'Autoreloader'.
[12/Nov/2021:11:37:28] ENGINE Serving on http://127.0.0.1:8080
[12/Nov/2021:11:37:28] ENGINE Bus STARTED


127.0.0.1 - - [12/Nov/2021:11:37:30] "GET /?code=4de6523d9fa3c4c25e8557e80cebeb15e16a73c8&state=aQI5KnJYc1G1si0Yt2ULbwN8UXIdfy HTTP/1.1" 200 122 "" "Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/95.0.4638.54 Safari/537.36"


[12/Nov/2021:11:37:31] ENGINE Bus STOPPING
[12/Nov/2021:11:37:31] ENGINE HTTP Server cherrypy._cpwsgi_server.CPWSGIServer(('127.0.0.1', 8080)) shut down
[12/Nov/2021:11:37:31] ENGINE Stopped thread 'Autoreloader'.
[12/Nov/2021:11:37:31] ENGINE Bus STOPPED
[12/Nov/2021:11:37:31] ENGINE Bus EXITING
[12/Nov/2021:11:37:31] ENGINE Bus EXITED
[12/Nov/2021:11:37:31] ENGINE Waiting for child threads to terminate...


In [22]:
## approval needed 
# https://dev.fitbit.com/build/reference/web-api/intraday-requests/

# look at 1min heart rate on marathon day
fit_statsHR = auth2_client.intraday_time_series('activities/heart', base_date="2021-09-19", detail_level='1min')

time_list = []
val_list = []
for i in fit_statsHR['activities-heart-intraday']['dataset']:
    val_list.append(i['value'])
    time_list.append(i['time'])
heartdf = pd.DataFrame({'Heart Rate':val_list,'Time':time_list})
print(heartdf.shape)

fig = px.line(x=heartdf['Time'],y=heartdf['Heart Rate'])
fig.show()

(795, 2)


In [50]:
pull_data = False


if pull_data:
    # intraday heart rate for all time
    # got it for my bday last year!
    start_date = "2021-06-20"
    end_date = today


    #Rate Limit: 150 API requests per hour
    limit = 0
    rate = int(60*60/150) + 1# sleep seconds
    df_hr = pd.DataFrame()
    for d in pd.date_range(start=start_date,end=end_date,freq='d'):
        fit_statsHR = auth2_client.intraday_time_series('activities/heart', base_date=d.strftime('%Y-%m-%d'), detail_level='1min')

        time_list = []
        val_list = []
        for i in fit_statsHR['activities-heart-intraday']['dataset']:
            val_list.append(i['value'])
            time_list.append(i['time'])
        heartdf = pd.DataFrame({'Heart Rate':val_list,'Time':time_list,'Date':d})

        df_hr = df_hr.append(heartdf,ignore_index=True)
        time.sleep(rate)
        limit += 1
    # save buffer
    df_hr.to_csv('HeartRate1min'+today+'.csv')
else:
    df_hr = pd.read_csv('HeartRate1min20211112.csv',index_col=0)
print(df_hr.shape)
df_hr.head(2)

(134761, 3)


Heart Rate      Time        Date
0        70.0  17:51:00  2021-06-21
1        72.0  17:52:00  2021-06-21

In [51]:
df_hr['Datetime'] = pd.to_datetime(df_hr['Date'].astype(str) + ' ' + df_hr['Time'].astype(str))

fig = px.line(x=df_hr['Datetime'],y=df_hr['Heart Rate'])
fig.show()

In [55]:
fit_statsSl = auth2_client.sleep(date='today')
stime_list = []
sval_list = []
for i in fit_statsSl['sleep'][0]['minuteData']:
    stime_list.append(i['dateTime'])
    sval_list.append(i['value'])
sleepdf = pd.DataFrame({'State':sval_list,
                     'Time':stime_list})
sleepdf['Interpreted'] = sleepdf['State'].map({'2':'Awake','3':'Very Awake','1':'Asleep'})
sleepdf

State      Time Interpreted
0       3  23:20:00  Very Awake
1       2  23:21:00       Awake
2       2  23:22:00       Awake
3       2  23:23:00       Awake
4       1  23:24:00      Asleep
..    ...       ...         ...
533     1  08:13:00      Asleep
534     1  08:14:00      Asleep
535     1  08:15:00      Asleep
536     1  08:16:00      Asleep
537     1  08:17:00      Asleep

[538 rows x 3 columns]

In [66]:
fit_statsSum = auth2_client.sleep(date='today')['sleep'][0]
# last 90 days
start_date = (datetime.datetime.today() - datetime.timedelta(days=90)).strftime('%Y-%m-%d')
end_date = datetime.datetime.today().strftime('%Y-%m-%d')
df_sleep = pd.DataFrame()

for d in pd.date_range(start=start_date,end=end_date,freq='d'):
    try:
        fit_statsSum = auth2_client.sleep(date=d)['sleep'][0]
    except IndexError:
        continue
    ssummarydf = pd.DataFrame({'Date':fit_statsSum['dateOfSleep'],
                'MainSleep':fit_statsSum['isMainSleep'],
               'Efficiency':fit_statsSum['efficiency'],
               'Duration':fit_statsSum['duration'],
               'Minutes Asleep':fit_statsSum['minutesAsleep'],
               'Minutes Awake':fit_statsSum['minutesAwake'],
               'Awakenings':fit_statsSum['awakeCount'],
               'Restless Count':fit_statsSum['restlessCount'],
               'Restless Duration':fit_statsSum['restlessDuration'],
               'Time in Bed':fit_statsSum['timeInBed']
                        } ,index=[0])
    df_sleep = df_sleep.append(ssummarydf)
print(df_sleep.shape)
df_sleep.head()

(56, 10)


Date  MainSleep  Efficiency  Duration  Minutes Asleep  Minutes Awake  \
0  2021-07-22       True          90  29880000             450             48   
0  2021-07-23       True          90  34320000             511             57   
0  2021-07-25       True          98   5280000              86              2   
0  2021-07-26       True          96  27720000             444             18   
0  2021-07-27       True          98  25980000             425              8   

   Awakenings  Restless Count  Restless Duration  Time in Bed  
0           5              16                 34          498  
0           1               4                  6          572  
0           0               1                  2           88  
0           2               8                 12          462  
0           1               2                  5          433

In [71]:
df_sleep.describe()

Efficiency      Duration  Minutes Asleep  Minutes Awake  Awakenings  \
count   56.000000  5.600000e+01       56.000000      56.000000   56.000000   
mean    93.910714  2.538750e+07      397.607143      24.696429    1.178571   
std      4.200765  8.653195e+06      135.401045      15.436580    1.129878   
min     76.000000  4.560000e+06       61.000000       0.000000    0.000000   
25%     92.000000  2.259000e+07      357.000000      12.750000    0.000000   
50%     95.000000  2.718000e+07      423.000000      21.500000    1.000000   
75%     97.000000  3.046500e+07      484.250000      33.250000    2.000000   
max    100.000000  4.074000e+07      646.000000      74.000000    5.000000   

       Restless Count  Restless Duration  Time in Bed  
count       56.000000          56.000000    56.000000  
mean         9.767857          18.339286   423.125000  
std          5.138061          10.913339   144.219916  
min          0.000000           0.000000    76.000000  
25%          6.750000          11.000000   376.500000  
50%         10.000000          17.500000   453.000000  
75%         13.000000          25.000000   507.750000  
max         23.000000          57.000000   679.000000

In [72]:
df_sleep['MainSleep'].value_counts()

True     53
False     3
Name: MainSleep, dtype: int64

In [82]:
import plotly.express as px
fig = px.bar(df_sleep, x="Date", y="Time in Bed", title="Time in Bed last 90 Days")
fig.show()

fig = px.bar(df_sleep, x="Date", y="Minutes Awake", title="Minutes Awake last 90 Days")
fig.show()